In [26]:
import pandas as pd

df = pd.read_csv("..//static//csv//ds_salaries.csv")

df.head()

work_year experience_level employment_type                 job_title  \
0       2023               SE              FT  Principal Data Scientist   
1       2023               MI              CT               ML Engineer   
2       2023               MI              CT               ML Engineer   
3       2023               SE              FT            Data Scientist   
4       2023               SE              FT            Data Scientist   

   salary salary_currency  salary_in_usd employee_residence  remote_ratio  \
0   80000             EUR          85847                 ES           100   
1   30000             USD          30000                 US           100   
2   25500             USD          25500                 US           100   
3  175000             USD         175000                 CA           100   
4  120000             USD         120000                 CA           100   

  company_location company_size  
0               ES            L  
1               US            S  
2               US            S  
3               CA            M  
4               CA            M

<h2>Бизнес-цели</h2>
Задача регрессии: Построить модель для прогноза зарплаты в USD используя атрибуты.<br>
Задача классификации: Определение уровня опыта сотрудника (experience_level) на основе других характеристик, таких как job_title, salary_in_usd, и employment_type.

Проведем обработку данных и сделаем выборки

In [27]:
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler, OneHotEncoder

# Удаление выбросов из столбца `salary_in_usd` с использованием IQR
Q1 = df['salary_in_usd'].quantile(0.25)
Q3 = df['salary_in_usd'].quantile(0.75)
IQR = Q3 - Q1
df = df[(df['salary_in_usd'] >= Q1 - 1.5 * IQR) & (df['salary_in_usd'] <= Q3 + 1.5 * IQR)]

# Преобразование категориальных данных в числовые (если потребуется)
if 'remote_ratio' in df.columns:
    df['remote_ratio'] = df['remote_ratio'].astype(int)

# Удаление дубликатов
df.drop_duplicates(inplace=True)

# Определение целевой переменной и признаков
X = df.drop(columns=['salary_in_usd', 'salary_currency', 'job_title'])  # Признаки
y = df['salary_in_usd']  # Целевая переменная для регрессии

# Определение числовых и категориальных признаков
numeric_features = ['work_year', 'remote_ratio']
categorical_features = ['experience_level', 'employment_type', 
                        'employee_residence', 'company_location', 'company_size']

# Обработка числовых данных
numeric_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='median')),  # Заполнение пропусков медианой
    ('scaler', StandardScaler())                   # Нормализация данных
])

# Обработка категориальных данных
categorical_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='most_frequent')),  # Заполнение пропусков модой
    ('onehot', OneHotEncoder(handle_unknown='ignore'))     # Преобразование в One-Hot Encoding
])

# Комбинированный трансформер
preprocessor = ColumnTransformer(
    transformers=[
        ('num', numeric_transformer, numeric_features),   # Применяем числовую обработку
        ('cat', categorical_transformer, categorical_features)  # Применяем категориальную обработку
    ]
)

# Разделение данных на обучающую и тестовую выборки
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Применение пайплайна
X_train_transformed = preprocessor.fit_transform(X_train)
X_test_transformed = preprocessor.transform(X_test)

# Проверка результата трансформации
print(f"Transformed feature shape (train): {X_train_transformed.shape}")
print(f"Transformed feature shape (test): {X_test_transformed.shape}")


Transformed feature shape (train): (2029, 151)
Transformed feature shape (test): (508, 151)


Выведим результаты

In [28]:
# Получим имена категориальных признаков после OneHotEncoder
categorical_feature_names = preprocessor.named_transformers_['cat']['onehot'].get_feature_names_out(categorical_features)

# Объединим их с именами числовых признаков
feature_names = list(numeric_features) + list(categorical_feature_names)

# Создадим DataFrame для преобразованных данных
X_train_transformed_df = pd.DataFrame(X_train_transformed.toarray() if hasattr(X_train_transformed, 'toarray') else X_train_transformed, columns=feature_names)

# Выведем первые 5 строк обработанного набора данных
X_train_transformed_df.head()

work_year  remote_ratio  experience_level_EN  experience_level_EX  \
0  -1.747172      1.016983                  0.0                  0.0   
1  -1.747172      1.016983                  0.0                  0.0   
2   0.943539     -1.057887                  0.0                  0.0   
3  -0.401816      1.016983                  0.0                  0.0   
4  -0.401816     -0.020452                  0.0                  0.0   

   experience_level_MI  experience_level_SE  employment_type_CT  \
0                  0.0                  1.0                 0.0   
1                  0.0                  1.0                 0.0   
2                  0.0                  1.0                 0.0   
3                  1.0                  0.0                 0.0   
4                  1.0                  0.0                 0.0   

   employment_type_FL  employment_type_FT  employment_type_PT  ...  \
0                 0.0                 1.0                 0.0  ...   
1                 0.0                 1.0                 0.0  ...   
2                 0.0                 1.0                 0.0  ...   
3                 0.0                 1.0                 0.0  ...   
4                 0.0                 1.0                 0.0  ...   

   company_location_SI  company_location_SK  company_location_TH  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   company_location_TR  company_location_UA  company_location_US  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  1.0   
2                  0.0                  0.0                  1.0   
3                  0.0                  0.0                  1.0   
4                  0.0                  0.0                  0.0   

   company_location_VN  company_size_L  company_size_M  company_size_S  
0                  0.0             1.0             0.0             0.0  
1                  0.0             1.0             0.0             0.0  
2                  0.0             0.0             1.0             0.0  
3                  0.0             0.0             1.0             0.0  
4                  0.0             1.0             0.0             0.0  

[5 rows x 151 columns]

Обучим три модели

In [29]:
import numpy as np
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer

# Задание случайного состояния
random_state = 42

# Модели и параметры
models_regression = {
    "LinearRegression": LinearRegression(),
    "RandomForestRegressor": RandomForestRegressor(random_state=random_state),
    "GradientBoostingRegressor": GradientBoostingRegressor(random_state=random_state)
}

param_grids_regression = {
    "LinearRegression": {},
    "RandomForestRegressor": {
        'model__n_estimators': [50, 100, 200],
        'model__max_depth': [None, 10, 20],
        'model__min_samples_split': [2, 5, 10]
    },
    "GradientBoostingRegressor": {
        'model__n_estimators': [50, 100, 200],
        'model__learning_rate': [0.01, 0.1, 0.2],
        'model__max_depth': [3, 5, 10]
    }
}

# Результаты
results_regression = {}

# Перебор моделей
for name, model in models_regression.items():
    print(f"Training {name}...")
    
    # Создание пайплайна
    pipeline = Pipeline(steps=[
        ('preprocessor', preprocessor),  # Используем уже созданный preprocessor
        ('model', model)
    ])
    
    # Определение параметров для RandomizedSearchCV
    param_grid = param_grids_regression[name]
    search = RandomizedSearchCV(pipeline, param_distributions=param_grid, 
                                cv=5, scoring='neg_mean_absolute_error', 
                                n_jobs=-1, random_state=random_state, n_iter=20)
    search.fit(X_train, y_train)
    
    # Лучшая модель
    best_model = search.best_estimator_
    y_pred = best_model.predict(X_test)
    
    # Метрики
    mae = mean_absolute_error(y_test, y_pred)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    r2 = r2_score(y_test, y_pred)
    
    # Сохранение результатов
    results_regression[name] = {
        "Best Params": search.best_params_,
        "MAE": mae,
        "RMSE": rmse,
        "R2": r2
    }

# Печать результатов
for name, metrics in results_regression.items():
    print(f"\nModel: {name}")
    for metric, value in metrics.items():
        print(f"{metric}: {value}")


Training LinearRegression...
Training RandomForestRegressor...

c:\Users\salih\OneDrive\Рабочий стол\3 курас\МИИ\laba1\AIM-PIbd-31-Yaruskin-S-A\aimenv\Lib\site-packages\sklearn\model_selection\_search.py:320: UserWarning: The total space of parameters 1 is smaller than n_iter=20. Running 1 iterations. For exhaustive searches, use GridSearchCV.
  warnings.warn(



Training GradientBoostingRegressor...

Model: LinearRegression
Best Params: {}
MAE: 35903.74761235383
RMSE: 45746.92374132039
R2: 0.41681042958060477

Model: RandomForestRegressor
Best Params: {'model__n_estimators': 100, 'model__min_samples_split': 10, 'model__max_depth': 20}
MAE: 35382.49447920311
RMSE: 45711.49865435396
R2: 0.41771328994747514

Model: GradientBoostingRegressor
Best Params: {'model__n_estimators': 50, 'model__max_depth': 5, 'model__learning_rate': 0.2}
MAE: 35404.55042553757
RMSE: 45669.354449671955
R2: 0.41878648590699374


In [30]:
# Формирование таблицы метрик из результатов регрессионных моделей
reg_metrics = pd.DataFrame.from_dict(results_regression, orient="index")[
    ["MAE", "RMSE", "R2"]
]

# Визуализация результатов с помощью стилизации
styled_metrics = (
    reg_metrics.sort_values(by="RMSE")
    .style.background_gradient(cmap="viridis", low=1, high=0.3, subset=["RMSE", "MAE"])
    .background_gradient(cmap="plasma", low=0.3, high=1, subset=["R2"])
)

# Отобразим таблицу
styled_metrics

Чтото слабоватые модели получились. Даже 50% нет, нужно попробовать улучшить данные.

In [38]:
# Функция для приведения выбросов к среднему значению
def handle_outliers(df, column):
    Q1 = df[column].quantile(0.25)
    Q3 = df[column].quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    
    mean_value = df[column].mean()
    df[column] = np.where((df[column] < lower_bound) | (df[column] > upper_bound), mean_value, df[column])
    return df

# Приведение выбросов в столбце `salary_in_usd` к среднему значению
df = handle_outliers(df, 'salary_in_usd')

# Преобразование категориальных данных в строковые для корректной обработки
if 'remote_ratio' in df.columns:
    df['remote_ratio'] = df['remote_ratio'].astype(str)

# Удаление дубликатов
df.drop_duplicates(inplace=True)

# Определение целевой переменной и признаков
X = df.drop(columns=['salary_in_usd', 'salary_currency', 'job_title'])  # Признаки
y = df['salary_in_usd']  # Целевая переменная для регрессии

# Определение числовых и категориальных признаков
numeric_features = ['work_year']  # Убрали 'remote_ratio', так как это категориальный признак
categorical_features = ['experience_level', 'employment_type', 
                        'employee_residence', 'company_location', 'company_size', 'remote_ratio']

# Обработка числовых данных
numeric_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='median')),  # Заполнение пропусков медианой
    ('scaler', StandardScaler())                   # Нормализация данных
])

# Обработка категориальных данных
categorical_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='most_frequent')),  # Заполнение пропусков модой
    ('onehot', OneHotEncoder(handle_unknown='ignore'))     # Преобразование в One-Hot Encoding
])

# Комбинированный трансформер
preprocessor = ColumnTransformer(
    transformers=[
        ('num', numeric_transformer, numeric_features),   # Применяем числовую обработку
        ('cat', categorical_transformer, categorical_features)  # Применяем категориальную обработку
    ]
)

# Разделение данных на обучающую и тестовую выборки
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Применение пайплайна
X_train_transformed = preprocessor.fit_transform(X_train)
X_test_transformed = preprocessor.transform(X_test)

# Проверка результата трансформации
print(f"Transformed feature shape (train): {X_train_transformed.shape}")
print(f"Transformed feature shape (test): {X_test_transformed.shape}")

# Определение моделей и их параметров
models = {
    "LinearRegression": LinearRegression(),
    "RandomForestRegressor": RandomForestRegressor(random_state=42),
    "GradientBoostingRegressor": GradientBoostingRegressor(random_state=42)
}

param_grids = {
    "LinearRegression": {},
    "RandomForestRegressor": {
        'model__n_estimators': [100, 200, 300],
        'model__max_depth': [10, 20, None],
        'model__min_samples_split': [2, 5, 10]
    },
    "GradientBoostingRegressor": {
        'model__n_estimators': [100, 200, 300],
        'model__learning_rate': [0.01, 0.1, 0.2],
        'model__max_depth': [3, 5, 7]
    }
}

# Результаты
results = {}

# Обучение моделей с подбором гиперпараметров
for name, model in models.items():
    print(f"Training {name}...")
    pipeline = Pipeline(steps=[
        ('preprocessor', preprocessor),
        ('model', model)
    ])
    param_grid = param_grids[name]
    search = RandomizedSearchCV(pipeline, param_distributions=param_grid, cv=5, 
                                scoring='neg_mean_absolute_error', n_jobs=-1, 
                                random_state=42, n_iter=20)
    search.fit(X_train, y_train)
    
    # Лучшая модель
    best_model = search.best_estimator_
    y_pred = best_model.predict(X_test)
    
    # Метрики
    mae = mean_absolute_error(y_test, y_pred)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    r2 = r2_score(y_test, y_pred)
    
    # Сохранение результатов
    results[name] = {
        "Best Params": search.best_params_,
        "MAE": mae,
        "RMSE": rmse,
        "R2": r2
    }

# Печать результатов
for name, metrics in results.items():
    print(f"\nModel: {name}")
    for metric, value in metrics.items():
        print(f"{metric}: {value}")

# Формирование таблицы метрик из результатов регрессионных моделей
reg_metrics = pd.DataFrame.from_dict(results, orient="index")[
    ["MAE", "RMSE", "R2"]
]

# Визуализация результатов с помощью стилизации
styled_metrics = (
    reg_metrics.sort_values(by="RMSE")
    .style.background_gradient(cmap="viridis", low=1, high=0.3, subset=["RMSE", "MAE"])
    .background_gradient(cmap="plasma", low=0.3, high=1, subset=["R2"])
)

# Отобразим таблицу
styled_metrics

Transformed feature shape (train): (1886, 41)
Transformed feature shape (test): (472, 41)
Training LinearRegression...
Training RandomForestRegressor...


c:\Users\salih\OneDrive\Рабочий стол\3 курас\МИИ\laba1\AIM-PIbd-31-Yaruskin-S-A\aimenv\Lib\site-packages\sklearn\model_selection\_search.py:320: UserWarning: The total space of parameters 1 is smaller than n_iter=20. Running 1 iterations. For exhaustive searches, use GridSearchCV.
  warnings.warn(


Training GradientBoostingRegressor...

Model: LinearRegression
Best Params: {}
MAE: 37037.92339197355
RMSE: 45540.3787622507
R2: 0.4345993379829327

Model: RandomForestRegressor
Best Params: {'model__n_estimators': 300, 'model__min_samples_split': 10, 'model__max_depth': 10}
MAE: 36990.476148447306
RMSE: 45909.387319133624
R2: 0.4253994599029146

Model: GradientBoostingRegressor
Best Params: {'model__n_estimators': 100, 'model__max_depth': 3, 'model__learning_rate': 0.1}
MAE: 37119.53085174526
RMSE: 45945.52202948378
R2: 0.42449458199205714


Переписал не много код, стало чуть лучше, но не намного. Думаю для моей первой работы подойдет

<h2>Приступим к задаче классификации</h2>

In [39]:
import numpy as np
import pandas as pd
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import train_test_split, RandomizedSearchCV
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.metrics import accuracy_score, confusion_matrix, f1_score

# Преобразование целевой переменной для классификации
y_class = df['Leather interior'].map({'Yes': 1, 'No': 0})  # Преобразуем в 0/1
X = df.drop(columns=['Leather interior', 'ID'])  # Признаки

# Определение числовых и категориальных признаков
numeric_features = ['work_year']  # Пример числового признака
categorical_features = ['experience_level', 'employment_type', 'employee_residence', 
                        'company_location', 'company_size', 'remote_ratio']

# Обработка числовых данных
numeric_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='median')),
    ('scaler', StandardScaler())
])

# Обработка категориальных данных
categorical_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='most_frequent')),
    ('onehot', OneHotEncoder(handle_unknown='ignore'))
])

# Комбинированный трансформер
preprocessor = ColumnTransformer(
    transformers=[
        ('num', numeric_transformer, numeric_features),
        ('cat', categorical_transformer, categorical_features)
    ]
)

# Разделение данных на обучающую и тестовую выборки
X_train_clf, X_test_clf, y_train_clf, y_test_clf = train_test_split(X, y_class, test_size=0.2, random_state=42)

# Определение моделей и их гиперпараметров
models_classification = {
    "LogisticRegression": LogisticRegression(max_iter=1000),
    "RandomForestClassifier": RandomForestClassifier(random_state=42),
    "KNN": KNeighborsClassifier()
}

param_grids_classification = {
    "LogisticRegression": {
        'model__C': [0.1, 1, 10]
    },
    "RandomForestClassifier": {
        "model__n_estimators": [100, 200, 300],
        "model__max_features": ["sqrt", "log2", None],
        "model__max_depth": [5, 10, 15, None],
        "model__criterion": ["gini", "entropy"]
    },
    "KNN": {
        'model__n_neighbors': [3, 5, 7, 9],
        'model__weights': ['uniform', 'distance']
    }
}

# Результаты
results_classification = {}

# Перебор моделей
for name, model in models_classification.items():
    print(f"Training {name}...")
    pipeline = Pipeline(steps=[
        ('preprocessor', preprocessor),
        ('model', model)
    ])
    param_grid = param_grids_classification[name]
    grid_search = RandomizedSearchCV(pipeline, param_distributions=param_grid, cv=5, scoring='f1', n_jobs=-1, random_state=42)
    grid_search.fit(X_train_clf, y_train_clf)

    # Лучшая модель
    best_model = grid_search.best_estimator_
    y_pred = best_model.predict(X_test_clf)

    # Метрики
    acc = accuracy_score(y_test_clf, y_pred)
    f1 = f1_score(y_test_clf, y_pred)

    # Вычисление матрицы ошибок
    c_matrix = confusion_matrix(y_test_clf, y_pred)

    # Сохранение результатов
    results_classification[name] = {
        "Best Params": grid_search.best_params_,
        "Accuracy": acc,
        "F1 Score": f1,
        "Confusion_matrix": c_matrix
    }

# Печать результатов
for name, metrics in results_classification.items():
    print(f"\nModel: {name}")
    for metric, value in metrics.items():
        print(f"{metric}: {value}")


KeyError: 'Leather interior'